# Introduction




## Physical problem

This project models and visualizes a **damped harmonic oscillator** coupled to a simple mechanical representation of a **mass–spring system**. Physically, the system behaves as an underdamped single-degree-of-freedom oscillator, where the motion is governed by the second-order differential equation

$$
m\,\ddot{y} + c\,\dot{y} + k\,y = 0
$$

with $m$ as the mass, $k$ the spring stiffness, and $c$ the viscous damping coefficient. In the underdamped regime $(0 \le \zeta < 1)$, where the damping ratio is 

$$\zeta = \frac{c}{2\sqrt{km}}$$ 

the solution is oscillatory with an exponentially decaying amplitude:

$$
y(t) = A\,e^{-\zeta\omega_0 t} \cos(\omega_d t),
$$

where $\omega_0 = \sqrt{k/m}$ is the natural angular frequency and $\omega_d = \omega_0 \sqrt{1 - \zeta^2}$ is the damped angular frequency. The code implements this solution explicitly, computing the displacement at each frame rather than numerically integrating the equation of motion.

From a programming perspective, the animation has three main layers:

1. **Physics layer** — handled by functions that either compute $(\zeta, \omega_0, \omega_d)$ from physical parameters or accept them directly, and then generate the position–time data arrays for the oscillator’s horizontal and vertical motion.
2. **Graphics layer** — builds the scene using Matplotlib primitives: the moving particle, its trajectory trace, the spring polyline, the block, and decorative elements like arcs and a ceiling anchor.
3. **Animation engine** — a `FuncAnimation` object calls a frame update function that reads the precomputed motion arrays, updates the positions of all moving parts, and redraws only the changed elements for efficiency.

The result is a smooth, realistic animation of a damped oscillator moving left-to-right across the screen while a vertically oscillating mass–spring system on the right moves in phase with the particle’s vertical motion. This modular approach separates the physical model from the rendering logic, making it easy to modify parameters, change visual details, or export the animation to GIF or MP4 for inclusion in presentations or teaching materials.

# Functions
**`resolve_params`** function determines the physical parameters needed for the simulation: the damping ratio (`zeta`), the natural angular frequency (`omega0`), and the damped angular frequency (`omega_d`). It can accept these values directly or derive them from the mass–spring–damper parameters (`m`, `k`, `c`). It validates the input, ensuring the motion is in the underdamped regime (`0 <= zeta < 1`), which is required for oscillatory behavior. 

**`make_paths`** function precomputes the motion of the oscillator over time. Given the amplitude, damping ratio, frequencies, and time span, it generates arrays for the time (`t_path`), the horizontal position (`x_path`) that moves linearly across the screen, and the vertical displacement (`y_path`) that follows the damped cosine law of underdamped harmonic motion. 

**`make_spring`** function constructs the polyline representation of a vertical coil spring between two points, adding straight “tail” segments at the ends for realism and shaping the coil with a sinusoidal pattern. 

**`setup_scene`** function initializes the figure, axes, and all graphical elements required for the animation. It sets axis limits, hides axis ticks, draws the static background trajectory, and creates the matplotlib `Artist` objects for the moving particle, its trace, the ceiling, the block, the spring, and decorative arcs, returning these for later updates. 

**`animate_frame`** function is the core of the animation loop: for each frame index, it computes the corresponding position along the precomputed path, updates the particle’s position and the trace line, moves the block vertically in sync with the oscillation, recalculates the spring geometry, and adjusts the decorative arcs, returning the updated artists for efficient redrawing. 

**`create_damped_oscillator`** function orchestrates the simulation: it resolves the physical parameters, generates the motion paths, sets up the scene, builds a `state` dictionary with all relevant values, and creates the `FuncAnimation` object that drives the frame updates via `animate_frame`. It closes the figure to avoid displaying a static snapshot and returns the animation object for further use. 

**`save_animation`** function handles output, saving a `FuncAnimation` as either a GIF (via `PillowWriter`) or an MP4 (via ffmpeg) depending on the file extension, with error handling for unsupported formats.

## How it works

The process starts with **`resolve_params`**, which normalizes the physical inputs: if you provide $(m,k,c)$ it computes 

$$\omega_0= \sqrt{k/m}$$ 
and 
$$\zeta= \frac{c}{2\sqrt{km}}$$ 

otherwise it uses your $(\zeta,\omega\_0)$ directly, and derives the damped frequency 

$$\omega_d=\omega_0\sqrt{1-\zeta^2}$$

enforcing the underdamped regime. With those in hand, **`make_paths`** builds three arrays over the animation horizon: a linear horizontal march $x(t)$ for the marker, and the vertical displacement 

$$y(t)=A,e^{-\zeta \omega_0 t}\cos(\omega_d t)$$

which is the analytical solution of the underdamped oscillator. The drawing primitives come next: 

**`make_spring`** generates a polyline of the coil between current endpoints using a sinusoid (for the coils) plus short straight “tails” near the attachments so the spring looks physically plausible. 

**`setup_scene`** initializes the Matplotlib figure/axes and creates all artists (trace line, moving dot, ceiling block, mass block, spring, decorative arcs), returning them in a dictionary for fast updates. Runtime updates are handled by 

**`animate_frame`**: for each frame index it selects the corresponding \$(x,y)\$ from the precomputed paths, moves the dot, extends the trace, repositions the block using a scaled \$y(t)\$, recomputes the spring geometry to the block’s new top, and refreshes the small arcs; it returns only the modified artists to enable blitting. The orchestrator 

**`create_damped_oscillator`** wires everything: it resolves parameters, creates paths, sets up the scene, assembles a lightweight `state` dict, constructs a `FuncAnimation` that repeatedly calls `animate_frame`, closes the figure to avoid a static snapshot, and returns the animation object for further use. 

If you want a file, **`save_animation`** takes that `FuncAnimation` and writes it to **GIF** (PillowWriter) or **MP4** (ffmpeg/H.264) based on the extension, controlling frame rate via `fps`. In short: physics → trajectories → artists → frame updates → returned animation (and, optionally, disk output).


## Functions

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation, PillowWriter
from matplotlib.patches import Rectangle, Circle
from IPython.display import HTML
from matplotlib.animation import PillowWriter


# Determines the damping ratio, natural frequency, and damped natural frequency
# Accepts either (zeta, omega0) directly or mass–spring–damper parameters (m, k, c)
# Returns (zeta, omega0, omega_d) for underdamped motion
def resolve_params(zeta=None, omega0=None, m=None, k=None, c=None):
    if any(v is not None for v in (m, k, c)):
        if None in (m, k, c):
            raise ValueError("If using (m,k,c), provide all three.")
        omega0 = np.sqrt(k / m)
        zeta = c / (2.0 * np.sqrt(k * m))
    if zeta is None or omega0 is None:
        raise ValueError("Provide either (zeta, omega0) or (m, k, c).")
    if not (0 <= zeta < 1):
        raise ValueError("Underdamped regime required: 0 <= zeta < 1.")
    omega_d = omega0 * np.sqrt(1 - zeta**2)
    return zeta, omega0, omega_d


# Precomputes the time array, horizontal path, and vertical displacement
# The vertical motion follows the standard underdamped harmonic oscillator solution
def make_paths(A, zeta, omega0, omega_d, duration, n_path, x_left, x_right):
    t_path = np.linspace(0.0, duration, n_path)
    x_path = np.linspace(x_left, x_right, n_path)
    y_path = A * np.exp(-zeta * omega0 * t_path) * np.cos(omega_d * t_path)
    return t_path, x_path, y_path


# Generates the coordinates of a vertical coil spring between two points
# Returns arrays of x and y coordinates for the spring polyline
def make_spring(xc, y_top, y_bottom, turns=8, width=0.28):
    L = y_top - y_bottom
    tail = 0.12 * L
    usable = L - 2 * tail
    N = max(40, turns * 40)
    s = np.linspace(0, usable, N)
    xs = xc + width * np.sin(2 * np.pi * turns * s / usable)
    ys = y_top - tail - s
    xs = np.r_[xc, xs, xc]
    ys = np.r_[y_top, ys, y_bottom]
    return xs, ys


# Sets up the entire scene for the animation
# Creates the figure, axes, static elements, and all the artists that will be updated
# Returns the figure, axis, and a dictionary of artists
def setup_scene(fig_size, xlim, ylim, x_path, y_path,
                spring_x, anchor_y_top, mass_w, mass_h, y_eq):
    fig, ax = plt.subplots(figsize=fig_size, dpi=100)
    ax.set_xlim(*xlim)
    ax.set_ylim(*ylim)
    ax.axis('off')

    ax.plot(x_path, y_path, lw=6, color='0.7', alpha=0.7, solid_capstyle='round')
    (trace_line,) = ax.plot([], [], lw=5, alpha=0.4, color='0.5', solid_capstyle='round')
    dot = Circle((x_path[0], y_path[0]), 0.08, ec='none', fc='#1f7a1f')
    ax.add_patch(dot)

    ceiling = Rectangle((spring_x-0.23, anchor_y_top+0.15), 0.46, 0.46, fc='0.7', ec='none')
    ax.add_patch(ceiling)
    mass_rect = Rectangle((spring_x-0.28, y_eq-mass_h/2), mass_w, mass_h, fc='#1f7a1f', ec='none')
    ax.add_patch(mass_rect)

    (spring_line,) = ax.plot([], [], lw=6, color='0.5')
    (arc1,) = ax.plot([], [], lw=4, color='0.6')
    (arc2,) = ax.plot([], [], lw=4, color='0.6')

    artists = {
        "trace_line": trace_line,
        "dot": dot,
        "mass_rect": mass_rect,
        "spring_line": spring_line,
        "arc1": arc1,
        "arc2": arc2,
    }
    return fig, ax, artists


# Updates the animation for a single frame
# Moves the particle, updates the trace, block, spring, and decorative arcs
def animate_frame(frame, state, artists):
    fps = state["fps"]
    frames = state["frames"]
    x_path = state["x_path"]
    y_path = state["y_path"]
    spring_x = state["spring_x"]
    anchor_y_top = state["anchor_y_top"]
    mass_w = state["mass_w"]
    mass_h = state["mass_h"]
    y_eq = state["y_eq"]

    trace_line = artists["trace_line"]
    dot = artists["dot"]
    mass_rect = artists["mass_rect"]
    spring_line = artists["spring_line"]
    arc1 = artists["arc1"]
    arc2 = artists["arc2"]

    idx = int((frame / (frames - 1)) * (len(x_path) - 1))
    x, y = x_path[idx], y_path[idx]

    dot.center = (x, y)
    trace_line.set_data(x_path[:idx+1], y_path[:idx+1])

    mass_cy = y_eq + 0.55 * y
    mass_rect.set_xy((spring_x - 0.28, mass_cy - mass_h/2))

    xs, ys = make_spring(spring_x, anchor_y_top, mass_cy + mass_h/2)
    spring_line.set_data(xs, ys)

    ang = np.linspace(-np.pi/4, np.pi/2, 30)
    arc1.set_data(spring_x + 0.23*np.cos(ang),
                  anchor_y_top + 0.15 + 0.23*np.sin(ang))
    ang2 = np.linspace(np.pi/4, -np.pi/2, 30)
    arc2.set_data(spring_x + 0.23*np.cos(ang2),
                  mass_cy + mass_h/2 + 0.02 + 0.23*np.sin(ang2))

    return dot, trace_line, mass_rect, spring_line, arc1, arc2


# Creates the damped oscillator animation
# Returns a FuncAnimation object without displaying a static frame
def create_damped_oscillator(
    A=1.0, zeta=None, omega0=None, m=None, k=None, c=None,
    duration=8.0, fps=30,
    fig_size=(8, 3.2), xlim=(0, 10), ylim=(-1.4, 1.4),
    n_path=1200, x_left=0.5, x_right=7.2,
    spring_x=8.7, anchor_y_top=1.0, mass_w=0.35, mass_h=0.45, y_eq=-0.1
):
    zeta, omega0, omega_d = resolve_params(zeta=zeta, omega0=omega0, m=m, k=k, c=c)
    _, x_path, y_path = make_paths(A, zeta, omega0, omega_d, duration, n_path, x_left, x_right)

    fig, ax, artists = setup_scene(fig_size, xlim, ylim, x_path, y_path,
                                   spring_x, anchor_y_top, mass_w, mass_h, y_eq)

    state = dict(A=A, zeta=zeta, omega0=omega0, omega_d=omega_d,
                 duration=duration, fps=fps, frames=int(duration*fps),
                 x_path=x_path, y_path=y_path,
                 spring_x=spring_x, anchor_y_top=anchor_y_top,
                 mass_w=mass_w, mass_h=mass_h, y_eq=y_eq)

    anim = FuncAnimation(fig, animate_frame, frames=state["frames"],
                         interval=1000/fps, blit=True,
                         fargs=(state, artists))

    plt.close(fig)
    return anim


# Saves a FuncAnimation object to a GIF or MP4 file
# Supports PillowWriter for GIF and ffmpeg for MP4
def save_animation(anim, filepath, fps=30):
    ext = filepath.lower().split('.')[-1]
    if ext == "gif":
        anim.save(filepath, writer=PillowWriter(fps=fps))
    elif ext == "mp4":
        anim.save(filepath, fps=fps, extra_args=['-vcodec', 'libx264'])
    else:
        raise ValueError("Unsupported format. Use .gif or .mp4")


# Pipeline

In [2]:
# Criar animação
anim = create_damped_oscillator(zeta=0.08, omega0=2*np.pi/1.6)

# Salvar em GIF
save_animation(anim, "oscillator.gif", fps=30)

# Salvar em MP4
save_animation(anim, "oscillator.mp4", fps=30)
HTML(anim.to_jshtml())